In [1]:
import pandas as pd
import numpy as np
import pickle
from datetime import timedelta
import os

import math
import tensorflow as tf
import random

import keras
from keras.layers import LSTM, Dense

from keras.models import Sequential 
from keras.layers import Dense, Dropout
from keras.optimizers import Adam, RMSprop
from keras.callbacks import EarlyStopping 
from scikeras.wrappers import KerasRegressor
from keras.models import load_model
from sklearn.model_selection import KFold

random.seed(123)
np.random.seed(123)
tf.random.set_seed(123)
import gc
import pickle

from sklearn.preprocessing import LabelEncoder
from sklearn.svm import SVR
from sklearn.model_selection import RandomizedSearchCV
from sklearn.preprocessing import StandardScaler, MinMaxScaler
from sklearn.model_selection import train_test_split
from sklearn.metrics import  mean_absolute_error, mean_squared_error, mean_absolute_percentage_error

from sklearn.ensemble import RandomForestRegressor

import plotly.express as px
import plotly.graph_objects as go

def CVRMSE(y_pred, y_true):
    y_pred, y_true = np.array(y_pred), np.array(y_true)
    return mean_squared_error(y_true,y_pred, squared=False)/np.mean(y_true)*100

# Stack data 

In [2]:
# Read the kc dates and its values
fechas_kc = pd.read_excel('./kc_2023.xlsx', usecols='B:D')
fechas_kc.dropna(inplace=True)
fechas_kc

Start        End    Kc
0  2023-04-10 2023-04-16  0.55
1  2023-04-17 2023-04-23  0.55
2  2023-04-24 2023-04-30  0.55
3  2023-05-01 2023-05-07  0.55
4  2023-05-08 2023-05-14  0.55
5  2023-05-15 2023-05-21  0.55
6  2023-05-22 2023-05-28  0.55
7  2023-05-29 2023-06-04  0.55
8  2023-06-05 2023-06-11  0.58
9  2023-06-12 2023-06-18  0.62
10 2023-06-19 2023-06-25  0.62
11 2023-06-26 2023-07-02  0.68
12 2023-07-03 2023-07-09  0.68
13 2023-07-10 2023-07-16  0.68
14 2023-07-17 2023-07-23  0.68
15 2023-07-24 2023-07-30  0.68
16 2023-07-31 2023-08-06  0.68
17 2023-08-07 2023-08-13  0.68
18 2023-08-14 2023-08-20  0.55
19 2023-08-21 2023-08-27  0.55
20 2023-08-28 2023-09-03  0.49
21 2023-09-04 2023-09-10  0.49
22 2023-09-11 2023-09-17  0.49
23 2023-09-18 2023-09-24  0.46
24 2023-09-25 2023-10-01  0.46
25 2023-10-02 2023-10-08  0.39
26 2023-10-09 2023-10-15  0.39
27 2023-10-16 2023-10-22  0.36
28 2023-10-23 2023-10-29  0.36

In [3]:
# Find the corresponding kc value of the date x
def getKc(x):
    for i in range(0,len(fechas_kc)):
        if (x >= fechas_kc['Start'][i]) & (x < fechas_kc['End'][i] + timedelta(days=1)):
            return fechas_kc['Kc'][i]

## Read data

In [4]:
plots = os.listdir('./datos 2023/')
all_plots = []

# Read plots one by one and save them in a array
for p in plots:
    # Read data
    df_fp = pd.read_excel('./datos 2023/' + p, usecols='E,F,J,N,R,W, Y:AE')
    df_fp['DateTime'] = pd.to_datetime(df_fp['DateTime'])

    # Use the hour as one of input variables (applying sin to avoid jump from 23 to 00)
    df_fp['hour_sin'] = df_fp['DateTime'].apply(lambda x: math.sin( (2 * math.pi * x.hour) / 24) )
    df_fp.set_index('DateTime',inplace=True)

    # Resample the FP values
    df_fp = df_fp.resample('1h').mean() # Resampling de 1h
    df_fp.columns = ['FP', 'HR5_25', 'HR35_55', 'HR65_85', 'Riego', 'TMED', 'PREC', 'HR', 'RAD', 'DPV', 'VV', 'ETO', 'Hour_sin']

    # Use only HR_35_55 and data from 2023-6-1
    df_fp.drop(columns=['HR5_25', 'HR65_85', ], inplace=True)
    df_fp = df_fp[df_fp.index >= '2023-6-1'].copy()

    # Set the kc value for each date (row) using the function getKc()
    kcs = df_fp.reset_index()['DateTime'].apply(lambda x: getKc(x))
    df_fp['Kc'] = kcs.values

    # Categorical input variable (name of the plot)
    df_fp['ID'] = p.split('_')[0]

    # Delete the malfunction part of the plot T4.2.
    if '4.2' in p.split('_')[0]: 
        df_fp = df_fp[(df_fp.index >= '2023-07-26 12:00:00')]
    df_fp = df_fp[(df_fp.index <= '2023-10-1 00:00:00')]

    # Move/shift a line to all input variables (we use the present input variables to predict the next hour FP)
    for c in df_fp.columns[1:]:
        df_fp[c] = df_fp[c].shift(1)

    # Create a new columnn as the lag of previous FP
    df_fp['FP-lag1'] = df_fp['FP'].shift(1)

    df_fp.dropna(inplace=True)
    all_plots.append(df_fp)
all_plots

[                            FP    HR35_55     Riego       TMED  PREC   
 DateTime                                                               
 2023-07-21 10:00:00  -3.614804  62.354863  0.000000  26.946250   0.0  \
 2023-07-21 11:00:00  -2.526165  59.446942  1.554878  29.925000   0.0   
 2023-07-21 12:00:00  -3.653391  58.095185  0.762195  31.916250   0.0   
 2023-07-21 13:00:00  -8.117500  57.229654  0.000000  33.187500   0.0   
 2023-07-21 14:00:00  -9.626121  56.622889  0.000000  34.270000   0.0   
 ...                        ...        ...       ...        ...   ...   
 2023-09-30 20:00:00 -12.522581  44.335860  0.000000  25.678750   0.0   
 2023-09-30 21:00:00 -10.869316  44.345736  0.000000  22.625000   0.0   
 2023-09-30 22:00:00 -10.028503  44.353496  0.000000  17.862917   0.0   
 2023-09-30 23:00:00  -9.456029  44.363735  0.000000  16.011250   0.0   
 2023-10-01 00:00:00  -9.008149  44.379830  0.000000  15.433333   0.0   
 
                             HR        RAD       

In [5]:
# Combine all plot in a df to train the scalers with all possible values
df_all_plots = pd.concat(all_plots)
numerical_features = ['HR35_55', 'Riego', 'TMED', 'PREC', 'HR', 'RAD', 'DPV', 'VV', 'ETO', 'Hour_sin', 'Kc', 'FP-lag1']
scaler_x = MinMaxScaler().fit(df_all_plots[numerical_features])
scaler_y = MinMaxScaler().fit(df_all_plots[['FP']])

In [6]:
fig = go.Figure()
for p in all_plots:
    fig.add_trace(go.Scatter(x=p.index, y=p['FP']*0.1,
                    name=p['ID'][0], mode='lines'))
fig.show()

## Prepare data

In [102]:
# split the train(0.7)/test(0.3) set for each plot 
train = pd.DataFrame()
test = pd.DataFrame()
for p in all_plots:
    train = pd.concat([train, p.iloc[:int(len(p)*0.7),:]])
    test = pd.concat([test, p.iloc[int(len(p)*0.7):,:]])
    print(p['ID'][0] + ':', len(p), 'observations -> train:', len(train), ', test:', len(test))

T1.1.: 1719 observations -> train: 1203 , test: 516
T1.2.: 2928 observations -> train: 3252 , test: 1395
T2.1.: 2928 observations -> train: 5301 , test: 2274
T2.2.: 2928 observations -> train: 7350 , test: 3153
T3.1.: 2928 observations -> train: 9399 , test: 4032
T4.1.: 2928 observations -> train: 11448 , test: 4911
T4.2.: 1596 observations -> train: 12565 , test: 5390


In [103]:
# Encode Observation_ID
encoder = LabelEncoder()
train['ID_encoded'] = encoder.fit_transform(train['ID'])
test['ID_encoded'] = encoder.fit_transform(test['ID'])
display(train)
display(test)

FP    HR35_55     Riego       TMED  PREC   
DateTime                                                               
2023-07-21 10:00:00  -3.614804  62.354863  0.000000  26.946250   0.0  \
2023-07-21 11:00:00  -2.526165  59.446942  1.554878  29.925000   0.0   
2023-07-21 12:00:00  -3.653391  58.095185  0.762195  31.916250   0.0   
2023-07-21 13:00:00  -8.117500  57.229654  0.000000  33.187500   0.0   
2023-07-21 14:00:00  -9.626121  56.622889  0.000000  34.270000   0.0   
...                        ...        ...       ...        ...   ...   
2023-09-10 21:00:00 -11.066156  70.488051  0.000000  24.480000   0.0   
2023-09-10 22:00:00 -10.182823  70.401948  0.000000  22.856250   0.0   
2023-09-10 23:00:00  -9.456375  70.347922  0.000000  21.865000   0.0   
2023-09-11 00:00:00  -8.862500  70.254918  0.000000  20.642917   0.0   
2023-09-11 01:00:00  -8.166159  70.215309  0.000000  19.426250   0.0   

                            HR        RAD       DPV        VV       ETO   
DateTime                                                                  
2023-07-21 10:00:00  30.140417  527.15625  2.497250  1.173625  0.396445  \
2023-07-21 11:00:00  25.113000  734.73850  3.183800  1.044950  0.553319   
2023-07-21 12:00:00  21.367500  863.03250  3.729250  1.068750  0.659422   
2023-07-21 13:00:00  18.329643  949.59750  4.158536  1.264286  0.739059   
2023-07-21 14:00:00  15.195000  988.50000  4.580750  1.341000  0.779942   
...                        ...        ...       ...       ...       ...   
2023-09-10 21:00:00  53.927500    2.61250  1.438125  0.908125  0.060283   
2023-09-10 22:00:00  65.673750    0.00000  0.963750  0.849750  0.036168   
2023-09-10 23:00:00  70.256250    0.00000  0.780750  1.022750  0.036593   
2023-09-11 00:00:00  71.587917    0.00000  0.694208  0.645583  0.027003   
2023-09-11 01:00:00  74.343750    0.00000  0.580625  0.501500  0.021908   

                         Hour_sin    Kc     ID    FP-lag1  ID_encoded  
DateTime                                                               
2023-07-21 10:00:00  7.071068e-01  0.68  T1.1.  -3.645243           0  
2023-07-21 11:00:00  5.000000e-01  0.68  T1.1.  -3.614804           0  
2023-07-21 12:00:00  2.588190e-01  0.68  T1.1.  -2.526165           0  
2023-07-21 13:00:00  1.224647e-16  0.68  T1.1.  -3.653391           0  
2023-07-21 14:00:00 -2.588190e-01  0.68  T1.1.  -8.117500           0  
...                           ...   ...    ...        ...         ...  
2023-09-10 21:00:00 -8.660254e-01  0.49  T4.2. -12.285186           6  
2023-09-10 22:00:00 -7.071068e-01  0.49  T4.2. -11.066156           6  
2023-09-10 23:00:00 -5.000000e-01  0.49  T4.2. -10.182823           6  
2023-09-11 00:00:00 -2.588190e-01  0.49  T4.2.  -9.456375           6  
2023-09-11 01:00:00  0.000000e+00  0.49  T4.2.  -8.862500           6  

[12565 rows x 15 columns]

FP    HR35_55     Riego       TMED  PREC   
DateTime                                                               
2023-09-09 13:00:00 -14.827903  47.867593  3.636760  26.102857   0.0  \
2023-09-09 14:00:00 -16.106366  48.830717  0.514482  27.418750   0.0   
2023-09-09 15:00:00 -16.158395  49.292000  0.000000  28.536000   0.0   
2023-09-09 16:00:00 -16.440883  49.587850  0.000000  30.018333   0.0   
2023-09-09 17:00:00 -16.635155  49.737060  0.000000  30.351250   0.0   
...                        ...        ...       ...        ...   ...   
2023-09-30 20:00:00 -14.322500  68.474847  0.000000  25.813214   0.0   
2023-09-30 21:00:00 -12.811929  68.563167  0.000000  22.253750   0.0   
2023-09-30 22:00:00 -11.750043  68.643967  0.000000  17.947143   0.0   
2023-09-30 23:00:00 -11.012978  68.675542  0.000000  16.011250   0.0   
2023-10-01 00:00:00 -10.360000  68.705113  0.000000  15.432000   0.0   

                            HR         RAD       DPV        VV       ETO   
DateTime                                                                   
2023-09-09 13:00:00  49.861429  818.484286  1.705857  1.303286  0.569368  \
2023-09-09 14:00:00  45.186250  850.793750  2.006125  1.619125  0.607774   
2023-09-09 15:00:00  41.448000  822.189000  2.293700  1.877200  0.605895   
2023-09-09 16:00:00  33.210417  712.335000  2.842625  1.984250  0.552530   
2023-09-09 17:00:00  30.151250  593.298750  3.025250  1.939000  0.472046   
...                        ...         ...       ...       ...       ...   
2023-09-30 20:00:00  33.000357   24.374286  2.240357  0.841714  0.095524   
2023-09-30 21:00:00  42.021250    0.000000  1.610250  0.587625  0.044934   
2023-09-30 22:00:00  56.278571    0.000000  0.918143  0.579429  0.033200   
2023-09-30 23:00:00  63.022500    0.000000  0.675750  0.489875  0.026003   
2023-10-01 00:00:00  65.768000    0.000000  0.600700  0.484100  0.024190   

                         Hour_sin    Kc     ID    FP-lag1  ID_encoded  
DateTime                                                               
2023-09-09 13:00:00  1.224647e-16  0.49  T1.1. -13.954909           0  
2023-09-09 14:00:00 -2.588190e-01  0.49  T1.1. -14.827903           0  
2023-09-09 15:00:00 -5.000000e-01  0.49  T1.1. -16.106366           0  
2023-09-09 16:00:00 -7.071068e-01  0.49  T1.1. -16.158395           0  
2023-09-09 17:00:00 -8.660254e-01  0.49  T1.1. -16.440883           0  
...                           ...   ...    ...        ...         ...  
2023-09-30 20:00:00 -9.659258e-01  0.46  T4.2. -15.735960           6  
2023-09-30 21:00:00 -8.660254e-01  0.46  T4.2. -14.322500           6  
2023-09-30 22:00:00 -7.071068e-01  0.46  T4.2. -12.811929           6  
2023-09-30 23:00:00 -5.000000e-01  0.46  T4.2. -11.750043           6  
2023-10-01 00:00:00 -2.588190e-01  0.46  T4.2. -11.012978           6  

[5390 rows x 15 columns]

In [104]:
# scale the train and test data
train_scaled = train.copy()
train_scaled[numerical_features] = scaler_x.transform(train[numerical_features])
train_scaled['FP'] = scaler_y.transform(train[['FP']])
display(train_scaled)

test_scaled = test.copy()
test_scaled[numerical_features] = scaler_x.transform(test[numerical_features])
test_scaled

FP   HR35_55     Riego      TMED  PREC        HR   
DateTime                                                                      
2023-07-21 10:00:00  0.912509  0.585796  0.000000  0.510532   0.0  0.250270  \
2023-07-21 11:00:00  0.949747  0.528868  0.258228  0.601499   0.0  0.194319   
2023-07-21 12:00:00  0.911189  0.502404  0.126582  0.662310   0.0  0.152634   
2023-07-21 13:00:00  0.758491  0.485460  0.000000  0.701132   0.0  0.118825   
2023-07-21 14:00:00  0.706887  0.473581  0.000000  0.734190   0.0  0.083938   
...                       ...       ...       ...       ...   ...       ...   
2023-09-10 21:00:00  0.657630  0.745018  0.000000  0.435216   0.0  0.515004   
2023-09-10 22:00:00  0.687845  0.743333  0.000000  0.385628   0.0  0.645732   
2023-09-10 23:00:00  0.712694  0.742275  0.000000  0.355357   0.0  0.696732   
2023-09-11 00:00:00  0.733008  0.740454  0.000000  0.318036   0.0  0.711553   
2023-09-11 01:00:00  0.756826  0.739679  0.000000  0.280880   0.0  0.742223   

                          RAD       DPV        VV       ETO  Hour_sin   
DateTime                                                                
2023-07-21 10:00:00  0.504765  0.322311  0.158033  0.465367  0.853553  \
2023-07-21 11:00:00  0.703530  0.412610  0.140469  0.654406  0.750000   
2023-07-21 12:00:00  0.826375  0.484351  0.143718  0.782263  0.629410   
2023-07-21 13:00:00  0.909263  0.540813  0.170408  0.878227  0.500000   
2023-07-21 14:00:00  0.946513  0.596346  0.180879  0.927492  0.370590   
...                       ...       ...       ...       ...       ...   
2023-09-10 21:00:00  0.002502  0.183008  0.121793  0.060282  0.066987   
2023-09-10 22:00:00  0.000000  0.120615  0.113825  0.031224  0.146447   
2023-09-10 23:00:00  0.000000  0.096546  0.137439  0.031735  0.250000   
2023-09-11 00:00:00  0.000000  0.085163  0.085957  0.020179  0.370590   
2023-09-11 01:00:00  0.000000  0.070224  0.066290  0.014040  0.500000   

                           Kc     ID   FP-lag1  ID_encoded  
DateTime                                                    
2023-07-21 10:00:00  1.000000  T1.1.  0.897742           0  
2023-07-21 11:00:00  1.000000  T1.1.  0.898768           0  
2023-07-21 12:00:00  1.000000  T1.1.  0.935445           0  
2023-07-21 13:00:00  1.000000  T1.1.  0.897468           0  
2023-07-21 14:00:00  1.000000  T1.1.  0.747069           0  
...                       ...    ...       ...         ...  
2023-09-10 21:00:00  0.136364  T4.2.  0.606657           6  
2023-09-10 22:00:00  0.136364  T4.2.  0.647727           6  
2023-09-10 23:00:00  0.136364  T4.2.  0.677487           6  
2023-09-11 00:00:00  0.136364  T4.2.  0.701961           6  
2023-09-11 01:00:00  0.136364  T4.2.  0.721970           6  

[12565 rows x 15 columns]

FP   HR35_55     Riego      TMED  PREC        HR   
DateTime                                                                       
2023-09-09 13:00:00 -14.827903  0.302180  0.603978  0.484776   0.0  0.469752  \
2023-09-09 14:00:00 -16.106366  0.321035  0.085443  0.524962   0.0  0.417720   
2023-09-09 15:00:00 -16.158395  0.330065  0.000000  0.559081   0.0  0.376116   
2023-09-09 16:00:00 -16.440883  0.335857  0.000000  0.604350   0.0  0.284437   
2023-09-09 17:00:00 -16.635155  0.338778  0.000000  0.614517   0.0  0.250391   
...                        ...       ...       ...       ...   ...       ...   
2023-09-30 20:00:00 -14.322500  0.705606  0.000000  0.475931   0.0  0.282100   
2023-09-30 21:00:00 -12.811929  0.707335  0.000000  0.367229   0.0  0.382496   
2023-09-30 22:00:00 -11.750043  0.708917  0.000000  0.235710   0.0  0.541170   
2023-09-30 23:00:00 -11.012978  0.709535  0.000000  0.176590   0.0  0.616225   
2023-10-01 00:00:00 -10.360000  0.710114  0.000000  0.158901   0.0  0.646781   

                          RAD       DPV        VV       ETO  Hour_sin   
DateTime                                                                
2023-09-09 13:00:00  0.783719  0.218222  0.175732  0.673745  0.500000  \
2023-09-09 14:00:00  0.814656  0.257715  0.218843  0.720025  0.370590   
2023-09-09 15:00:00  0.787266  0.295539  0.254069  0.717761  0.250000   
2023-09-09 16:00:00  0.682078  0.367737  0.268681  0.653454  0.146447   
2023-09-09 17:00:00  0.568098  0.391757  0.262505  0.556469  0.066987   
...                       ...       ...       ...       ...       ...   
2023-09-30 20:00:00  0.023339  0.288523  0.112728  0.102749  0.017037   
2023-09-30 21:00:00  0.000000  0.205647  0.078046  0.041786  0.066987   
2023-09-30 22:00:00  0.000000  0.114617  0.076927  0.027647  0.146447   
2023-09-30 23:00:00  0.000000  0.082736  0.064703  0.018974  0.250000   
2023-10-01 00:00:00  0.000000  0.072864  0.063915  0.016789  0.370590   

                           Kc     ID   FP-lag1  ID_encoded  
DateTime                                                    
2023-09-09 13:00:00  0.136364  T1.1.  0.550403           0  
2023-09-09 14:00:00  0.136364  T1.1.  0.520991           0  
2023-09-09 15:00:00  0.136364  T1.1.  0.477919           0  
2023-09-09 16:00:00  0.136364  T1.1.  0.476166           0  
2023-09-09 17:00:00  0.136364  T1.1.  0.466649           0  
...                       ...    ...       ...         ...  
2023-09-30 20:00:00  0.000000  T4.2.  0.490398           6  
2023-09-30 21:00:00  0.000000  T4.2.  0.538018           6  
2023-09-30 22:00:00  0.000000  T4.2.  0.588911           6  
2023-09-30 23:00:00  0.000000  T4.2.  0.624686           6  
2023-10-01 00:00:00  0.000000  T4.2.  0.649518           6  

[5390 rows x 15 columns]

# 1h 

In [105]:

# Create the sequences (inputs) to train the models, assuming a sequence length of 12
sequence_length = 12
sequences = []
for obs_id in train_scaled['ID'].unique():
    obs_data = train_scaled[train_scaled['ID'] == obs_id]
    for i in range(len(obs_data) - sequence_length + 1):
        seq = obs_data.iloc[i:i + sequence_length]
        sequences.append(seq)

sequences

[                           FP   HR35_55     Riego      TMED  PREC        HR   
 DateTime                                                                      
 2023-07-21 10:00:00  0.912509  0.585796  0.000000  0.510532   0.0  0.250270  \
 2023-07-21 11:00:00  0.949747  0.528868  0.258228  0.601499   0.0  0.194319   
 2023-07-21 12:00:00  0.911189  0.502404  0.126582  0.662310   0.0  0.152634   
 2023-07-21 13:00:00  0.758491  0.485460  0.000000  0.701132   0.0  0.118825   
 2023-07-21 14:00:00  0.706887  0.473581  0.000000  0.734190   0.0  0.083938   
 2023-07-21 15:00:00  0.681671  0.463268  0.000000  0.755262   0.0  0.069832   
 2023-07-21 16:00:00  0.673316  0.450686  0.000000  0.780037   0.0  0.061207   
 2023-07-21 17:00:00  0.667749  0.437766  0.000000  0.776105   0.0  0.100117   
 2023-07-21 18:00:00  0.684981  0.420762  0.000000  0.729173   0.0  0.225416   
 2023-07-21 19:00:00  0.718675  0.405462  0.000000  0.678228   0.0  0.333930   
 2023-07-21 20:00:00  0.749874  0.392006

In [106]:
X_train = np.array([seq.drop(columns=['FP','ID']).values for seq in sequences])
y_train = np.array([seq['FP'].values[-1] for seq in sequences])

# Split data
X_features = X_train[:, :, :-1]  # numerical Features
X_obs_ids = X_train[:, :, -1]      # Observation_ID_encoded

In [15]:
from keras_tuner import HyperModel
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, LSTM, Dense, Embedding, Concatenate

class LSTMHyperModel(HyperModel):
    def build(self, hp):
        # Inputs
        numerical_input = Input(shape=(sequence_length, len(numerical_features)), name='Numerical_Input')
        categorical_input = Input(shape=(sequence_length,), name='Categorical_Input')
        
        # Embedding layer for categorical feature
        embedding_dim = hp.Int('embedding_dim', min_value=4, max_value=20, step=4)  # Tune embedding dimension
        num_observations = train_scaled['ID_encoded'].nunique()
        categorical_embedding = Embedding(input_dim=num_observations, 
                                          output_dim=embedding_dim, 
                                          input_length=sequence_length)(categorical_input)
        
        # Concatenate inputs
        concatenated = Concatenate()([numerical_input, categorical_embedding])
        
        # LSTM layers
        lstm_units_1 = hp.Int('lstm_units_1', min_value=16, max_value=128, step=8)  # Tune units in 1st LSTM
        lstm_out_1 = LSTM(lstm_units_1, activation="relu", return_sequences=True)(concatenated)

        lstm_units_2 = hp.Int('lstm_units_2', min_value=8, max_value=64, step=4)  # Tune units in 2nd LSTM
        lstm_out_2 = LSTM(lstm_units_2, activation="relu", return_sequences=False)(lstm_out_1)
        

        # Dense layer for final output
        output = Dense(1, activation='linear')(lstm_out_2)
        
        # Model
        model = Model(inputs=[numerical_input, categorical_input], outputs=output)
        
        # Compile
        learning_rate = hp.Float('learning_rate', min_value=1e-4, max_value=1e-2, sampling='log')  # Tune learning rate
        model.compile(optimizer=keras.optimizers.Adam(learning_rate=learning_rate), 
                      loss='mse', 
                      metrics=['mae'])
        
        return model

Using TensorFlow backend


In [90]:
X_features_train, X_features_val, X_obs_ids_train, X_obs_ids_val, y_train_train, y_train_val = train_test_split(X_features, X_obs_ids, y_train, test_size=0.2, shuffle=True, random_state=123)

In [17]:
from keras_tuner import RandomSearch, BayesianOptimization

# Initialize the tuner
tuner = BayesianOptimization(
    LSTMHyperModel(),
    objective='val_loss',  # Optimize for validation loss
    max_trials=20,         # Number of hyperparameter combinations to try
    executions_per_trial=1,  # Average results over 2 runs for each configuration
    directory='tuner_logs',  # Directory to save tuning logs
    project_name='lstm_hyperparameter_tuning_bayesian_1h',
    seed=1234
)

tuner.search(
    x=[X_features_train, X_obs_ids_train],
    y=y_train_train,
    validation_data=([X_features_val, X_obs_ids_val], y_train_val),
    epochs=70,
    batch_size=32,
    #callbacks=[tf.keras.callbacks.EarlyStopping(monitor='val_loss', patience=10)]  # Early stopping
)

Reloading Tuner from tuner_logs\lstm_hyperparameter_tuning_bayesian_1h\tuner0.json


In [18]:

lstm1h = tuner.get_best_models()[0]
lstm1h.summary()

Model: "model"
__________________________________________________________________________________________________
 Layer (type)                Output Shape                 Param #   Connected to                  
 Categorical_Input (InputLa  [(None, 12)]                 0         []                            
 yer)                                                                                             
                                                                                                  
 Numerical_Input (InputLaye  [(None, 12, 12)]             0         []                            
 r)                                                                                               
                                                                                                  
 embedding (Embedding)       (None, 12, 4)                28        ['Categorical_Input[0][0]']   
                                                                                              

In [107]:
r2s = []
maes = []
rmses = []
cvrmses = []
for id in test_scaled['ID'].unique():

    # Get df of corresponding plot
    df_plot = test_scaled[test_scaled['ID'] == id]

    # create sequences
    sequences = []
    for obs_id in df_plot['ID'].unique():
        obs_data = df_plot[df_plot['ID'] == obs_id]
        for i in range(len(obs_data) - sequence_length + 1):
            seq = obs_data.iloc[i:i + sequence_length]
            sequences.append(seq)

    # Create input/output 
    X_test = np.array([seq.drop(columns=['FP','ID']).values for seq in sequences])
    y_test = np.array([seq['FP'].values[-1] for seq in sequences])
    
    # Split numerical/categorical input
    X_features = X_test[:, :, :-1]  # numerical Features
    X_obs_ids = X_test[:, :, -1]      # Observation_ID_encoded

    # Make predictions on the test set
    y_pred = lstm1h.predict([X_features, X_obs_ids])
    y_pred = scaler_y.inverse_transform(y_pred).ravel()

    # Convert the unit bars to MPa
    y_pred = y_pred * 0.1
    y_test = y_test * 0.1

    # Metrics
    print('Plot:', id)
    r2 = np.corrcoef(y_test, y_pred)[0][1]**2
    r2s.append(r2)
    print('R2:', r2)
    mae = mean_absolute_error(y_true=y_test,y_pred=y_pred)
    maes.append(mae)
    print('MAE:', mae)
    rmse = mean_squared_error(y_true=y_test,y_pred=y_pred, squared=False)
    rmses.append(rmse)
    print('RMSE:', rmse)
    cvrmse = CVRMSE(y_true=y_test,y_pred=y_pred)
    cvrmses.append(cvrmse)
    print('CVRMSE:', cvrmse)
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=df_plot.index, y=y_test,
                        name='real', mode='lines'))
    fig.add_trace(go.Scatter(x=df_plot.index, y=y_pred,
                        name='prediction', mode='lines'))
    fig.show()

16/16 [==============================] - 0s 3ms/step
Plot: T1.1.
R2: 0.9844522671154062
MAE: 0.024427603680513603
RMSE: 0.03401753909722337
CVRMSE: -3.0313675655334933


28/28 [==============================] - 0s 3ms/step
Plot: T1.2.
R2: 0.9778903230744617
MAE: 0.03511308252262851
RMSE: 0.0499668836590428
CVRMSE: -3.7132850016062244


28/28 [==============================] - 0s 4ms/step
Plot: T2.1.
R2: 0.9733898858170216
MAE: 0.052437699692440005
RMSE: 0.07381516847628096
CVRMSE: -4.881100023515658


28/28 [==============================] - 0s 3ms/step
Plot: T2.2.
R2: 0.9883134575905861
MAE: 0.029583111344658502
RMSE: 0.03819260827825139
CVRMSE: -3.036626863135928


28/28 [==============================] - 0s 3ms/step
Plot: T3.1.
R2: 0.9882221540119083
MAE: 0.022470348337558562
RMSE: 0.030907138232623782
CVRMSE: -2.783844187879529


28/28 [==============================] - 0s 3ms/step
Plot: T4.1.
R2: 0.9745653520433059
MAE: 0.06272888858198551
RMSE: 0.08796927128683105
CVRMSE: -7.89218119511625


15/15 [==============================] - 0s 3ms/step
Plot: T4.2.
R2: 0.9914727493038555
MAE: 0.021999499927395073
RMSE: 0.028176247692017917
CVRMSE: -2.6376218724569203


In [108]:
# Overall metrics
print('R2:', np.mean(r2s))
print('MAE:',np.mean(maes))
print('RMSE:',np.mean(rmses))
print('CVRMSE:',np.mean(cvrmses))

R2: 0.982615169850935
MAE: 0.03553717629816854
RMSE: 0.04900640810318161
CVRMSE: -3.996575244177715


In [92]:
lstm1h.evaluate([X_features_val, X_obs_ids_val], y_train_val)

79/79 [==============================] - 1s 3ms/step - loss: 6.2668e-05 - mae: 0.0054


[6.266847776714712e-05, 0.005430520512163639]

# 6h

In [109]:
output_steps = 6  # Number of steps to predict
sequence_length = 12
sequences = []
targets = []

numerical_features_withID = ['HR35_55', 'Riego', 'TMED', 'PREC', 'HR', 'RAD', 'DPV', 'VV', 'ETO', 'Hour_sin', 'Kc', 'FP-lag1', 'ID_encoded']

for obs_id in train_scaled['ID'].unique():
    obs_data = train_scaled[train_scaled['ID'] == obs_id]
    for i in range(len(obs_data) - sequence_length - output_steps + 1):
        seq = obs_data.iloc[i:i + sequence_length]
        target_seq = obs_data.iloc[i + sequence_length-1:i + sequence_length + output_steps-1]['FP'].values
        sequences.append(seq[numerical_features_withID].values)
        targets.append(target_seq)

# Convert to numpy arrays
X_train = np.array(sequences)  # Shape: (num_sequences, sequence_length, num_features)
y_train = np.array(targets)  

# Split data
X_features = X_train[:, :, :-1]  # numerical Features
X_obs_ids = X_train[:, :, -1]      # Observation_ID_encoded

test = pd.concat(all_plots)
test['ID_encoded'] = encoder.transform(test['ID'])

test_scaled = test.copy()
test_scaled[numerical_features] = scaler_x.transform(test[numerical_features])
test_scaled

FP   HR35_55     Riego      TMED  PREC        HR   
DateTime                                                                       
2023-07-21 10:00:00  -3.614804  0.585796  0.000000  0.510532   0.0  0.250270  \
2023-07-21 11:00:00  -2.526165  0.528868  0.258228  0.601499   0.0  0.194319   
2023-07-21 12:00:00  -3.653391  0.502404  0.126582  0.662310   0.0  0.152634   
2023-07-21 13:00:00  -8.117500  0.485460  0.000000  0.701132   0.0  0.118825   
2023-07-21 14:00:00  -9.626121  0.473581  0.000000  0.734190   0.0  0.083938   
...                        ...       ...       ...       ...   ...       ...   
2023-09-30 20:00:00 -14.322500  0.705606  0.000000  0.475931   0.0  0.282100   
2023-09-30 21:00:00 -12.811929  0.707335  0.000000  0.367229   0.0  0.382496   
2023-09-30 22:00:00 -11.750043  0.708917  0.000000  0.235710   0.0  0.541170   
2023-09-30 23:00:00 -11.012978  0.709535  0.000000  0.176590   0.0  0.616225   
2023-10-01 00:00:00 -10.360000  0.710114  0.000000  0.158901   0.0  0.646781   

                          RAD       DPV        VV       ETO  Hour_sin   Kc   
DateTime                                                                     
2023-07-21 10:00:00  0.504765  0.322311  0.158033  0.465367  0.853553  1.0  \
2023-07-21 11:00:00  0.703530  0.412610  0.140469  0.654406  0.750000  1.0   
2023-07-21 12:00:00  0.826375  0.484351  0.143718  0.782263  0.629410  1.0   
2023-07-21 13:00:00  0.909263  0.540813  0.170408  0.878227  0.500000  1.0   
2023-07-21 14:00:00  0.946513  0.596346  0.180879  0.927492  0.370590  1.0   
...                       ...       ...       ...       ...       ...  ...   
2023-09-30 20:00:00  0.023339  0.288523  0.112728  0.102749  0.017037  0.0   
2023-09-30 21:00:00  0.000000  0.205647  0.078046  0.041786  0.066987  0.0   
2023-09-30 22:00:00  0.000000  0.114617  0.076927  0.027647  0.146447  0.0   
2023-09-30 23:00:00  0.000000  0.082736  0.064703  0.018974  0.250000  0.0   
2023-10-01 00:00:00  0.000000  0.072864  0.063915  0.016789  0.370590  0.0   

                        ID   FP-lag1  ID_encoded  
DateTime                                          
2023-07-21 10:00:00  T1.1.  0.897742           0  
2023-07-21 11:00:00  T1.1.  0.898768           0  
2023-07-21 12:00:00  T1.1.  0.935445           0  
2023-07-21 13:00:00  T1.1.  0.897468           0  
2023-07-21 14:00:00  T1.1.  0.747069           0  
...                    ...       ...         ...  
2023-09-30 20:00:00  T4.2.  0.490398           6  
2023-09-30 21:00:00  T4.2.  0.538018           6  
2023-09-30 22:00:00  T4.2.  0.588911           6  
2023-09-30 23:00:00  T4.2.  0.624686           6  
2023-10-01 00:00:00  T4.2.  0.649518           6  

[17955 rows x 15 columns]

In [22]:
from keras_tuner import HyperModel
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, LSTM, Dense, Embedding, Concatenate

class LSTMHyperModel(HyperModel):
    def build(self, hp):
        # Inputs
        numerical_input = Input(shape=(sequence_length, len(numerical_features)), name='Numerical_Input')
        categorical_input = Input(shape=(sequence_length,), name='Categorical_Input')
        
        # Embedding layer for categorical feature
        embedding_dim = hp.Int('embedding_dim', min_value=4, max_value=20, step=4)  # Tune embedding dimension
        num_observations = train_scaled['ID_encoded'].nunique()
        categorical_embedding = Embedding(input_dim=num_observations, 
                                          output_dim=embedding_dim, 
                                          input_length=sequence_length)(categorical_input)
        
        # Concatenate inputs
        concatenated = Concatenate()([numerical_input, categorical_embedding])
        
        # LSTM layers
        lstm_units_1 = hp.Int('lstm_units_1', min_value=16, max_value=128, step=8)  # Tune units in 1st LSTM
        lstm_out_1 = LSTM(lstm_units_1, activation="relu", return_sequences=True)(concatenated)

        lstm_units_2 = hp.Int('lstm_units_2', min_value=8, max_value=64, step=4)  # Tune units in 2nd LSTM
        lstm_out_2 = LSTM(lstm_units_2, activation="relu", return_sequences=False)(lstm_out_1)
        

        # Dense layer for final output
        output = Dense(output_steps, activation='linear')(lstm_out_2)
        
        # Model
        model = Model(inputs=[numerical_input, categorical_input], outputs=output)
        
        # Compile
        learning_rate = hp.Float('learning_rate', min_value=1e-4, max_value=1e-2, sampling='log')  # Tune learning rate
        model.compile(optimizer=keras.optimizers.Adam(learning_rate=learning_rate), 
                      loss='mse', 
                      metrics=['mae'])
        
        return model

In [85]:
X_features_train, X_features_val, X_obs_ids_train, X_obs_ids_val, y_train_train, y_train_val = train_test_split(X_features, X_obs_ids, y_train, test_size=0.2, shuffle=True, random_state=123)

In [24]:
from keras_tuner import BayesianOptimization

# Initialize the tuner
tuner = BayesianOptimization(
    LSTMHyperModel(),
    objective='val_loss',  # Optimize for validation loss
    max_trials=20,         # Number of hyperparameter combinations to try
    executions_per_trial=1,  # Average results over 2 runs for each configuration
    directory='tuner_logs',  # Directory to save tuning logs
    project_name='lstm_hyperparameter_tuning_bayesian_6h',
    seed=1234
)

tuner.search(
    x=[X_features_train, X_obs_ids_train],
    y=y_train_train,
    validation_data=([X_features_val, X_obs_ids_val], y_train_val),
    epochs=70,
    batch_size=32,
    #callbacks=[tf.keras.callbacks.EarlyStopping(monitor='val_loss', patience=10)]  # Early stopping
)



Reloading Tuner from tuner_logs\lstm_hyperparameter_tuning_bayesian_6h\tuner0.json


In [25]:
lstm_6h = tuner.get_best_models()[0]
lstm_6h.summary()

Model: "model"
__________________________________________________________________________________________________
 Layer (type)                Output Shape                 Param #   Connected to                  
 Categorical_Input (InputLa  [(None, 12)]                 0         []                            
 yer)                                                                                             
                                                                                                  
 Numerical_Input (InputLaye  [(None, 12, 12)]             0         []                            
 r)                                                                                               
                                                                                                  
 embedding (Embedding)       (None, 12, 4)                28        ['Categorical_Input[0][0]']   
                                                                                              

In [111]:


r2s = []
maes = []
rmses = []
cvrmses = []



for id in test_scaled['ID'].unique():
    print(id)

    # Get df of corresponding plot
    df_plot = test_scaled[test_scaled['ID'] == id]
    
    sequences = []
    targets = []

    # create sequences
    for obs_id in df_plot['ID'].unique():
        obs_data = df_plot[df_plot['ID'] == obs_id]
        for i in range(len(obs_data) - sequence_length - output_steps + 1):
            seq = obs_data.iloc[i:i + sequence_length]
            target_seq = obs_data.iloc[i + sequence_length:i + sequence_length + output_steps]['FP'].values
            sequences.append(seq[numerical_features_withID].values)
            targets.append(target_seq)

    # Convert to numpy arrays
    X_test = np.array(sequences)  # Shape: (num_sequences, sequence_length, num_features)
    y_test = np.array(targets)  
    
    # Split numerical/categorical input
    X_features = X_test[:, :, :-1]  # numerical Features
    X_obs_ids = X_test[:, :, -1]      # Observation_ID_encoded

    # Make predictions on the test set
    y_pred = lstm_6h.predict([X_features, X_obs_ids])
    y_pred = scaler_y.inverse_transform(y_pred)
    
    # Convert the unit bars to MPa
    y_pred = y_pred * 0.1
    y_test = y_test * 0.1
    
    #display(y_pred)

    # Initialize lists to store metrics for each step
    mae_per_step = []
    rmse_per_step = []
    r2_per_step = []
    cvrmse_per_step = []

    # Loop through each output step
    for step in range(output_steps):
        mae = mean_absolute_error(y_test[:, step], y_pred[:, step])  # MAE for step
        mae_per_step.append(mae)
        rmse = mean_squared_error(y_test[:, step], y_pred[:, step], squared=False)  # MAE for step
        rmse_per_step.append(rmse)
        r2 = np.corrcoef(y_test[:, step], y_pred[:, step])[0][1]**2  # R2 for step
        r2_per_step.append(r2)
        cvrmse = CVRMSE(y_test[:, step], y_pred[:, step])  # CVRMSE for step
        cvrmse_per_step.append(cvrmse)
        print(f"Step {step + 1}- R2: {r2:.4f} - MAE: {mae:.4f} - RMSE: {rmse:.4f} - CVRMSE: {cvrmse:.4f}")

    # Average metrics across all steps
    average_r2 = sum(r2_per_step) / output_steps
    r2s.append(average_r2)
    average_mae = sum(mae_per_step) / output_steps
    maes.append(average_mae)
    average_rmse = sum(rmse_per_step) / output_steps
    rmses.append(average_rmse)
    average_cvrmse = sum(cvrmse_per_step) / output_steps
    cvrmses.append(average_cvrmse)

    print("\nOverall Metrics:")
    print(f"Average R2 across all steps: {average_r2:.4f}")
    print(f"Average MAE across all steps: {average_mae:.4f}")
    print(f"Average RMSE across all steps: {average_rmse:.4f}")
    print(f"Average CVRMSE across all steps: {average_cvrmse:.4f}\n\n")



T1.1.
54/54 [==============================] - 0s 3ms/step
Step 1- R2: 0.9556 - MAE: 0.0732 - RMSE: 0.0920 - CVRMSE: -7.2922
Step 2- R2: 0.9509 - MAE: 0.0763 - RMSE: 0.0971 - CVRMSE: -7.6686
Step 3- R2: 0.9398 - MAE: 0.0831 - RMSE: 0.1077 - CVRMSE: -8.5324
Step 4- R2: 0.9229 - MAE: 0.0939 - RMSE: 0.1228 - CVRMSE: -9.6531
Step 5- R2: 0.9094 - MAE: 0.1018 - RMSE: 0.1338 - CVRMSE: -10.4799
Step 6- R2: 0.8957 - MAE: 0.1091 - RMSE: 0.1437 - CVRMSE: -11.2961

Overall Metrics:
Average R2 across all steps: 0.9291
Average MAE across all steps: 0.0896
Average RMSE across all steps: 0.1162
Average CVRMSE across all steps: -9.1537


T1.2.
91/91 [==============================] - 0s 3ms/step
Step 1- R2: 0.9613 - MAE: 0.0758 - RMSE: 0.0995 - CVRMSE: -9.4979
Step 2- R2: 0.9570 - MAE: 0.0803 - RMSE: 0.1045 - CVRMSE: -9.9016
Step 3- R2: 0.9501 - MAE: 0.0863 - RMSE: 0.1134 - CVRMSE: -10.7512
Step 4- R2: 0.9390 - MAE: 0.0959 - RMSE: 0.1260 - CVRMSE: -11.8609
Step 5- R2: 0.9302 - MAE: 0.1024 - RMSE: 0.135

In [113]:
# Overall metrics
print('R2:', np.mean(r2s))
print('MAE:',np.mean(maes))
print('RMSE:',np.mean(rmses))
print('CVRMSE:',np.mean(cvrmses))

R2: 0.930661537529331
MAE: 0.094868827450211
RMSE: 0.13278344326906039
CVRMSE: -12.947980118869893


In [87]:
lstm_6h.evaluate([X_features_val, X_obs_ids_val], y_train_val)

78/78 [==============================] - 0s 4ms/step - loss: 2.6715e-04 - mae: 0.0113


[0.0002671531110536307, 0.011338045820593834]

# 12h

In [116]:
output_steps = 12  # Number of steps to predict
sequence_length = 12
sequences = []
targets = []

numerical_features_withID = ['HR35_55', 'Riego', 'TMED', 'PREC', 'HR', 'RAD', 'DPV', 'VV', 'ETO', 'Hour_sin', 'Kc', 'FP-lag1', 'ID_encoded']

for obs_id in train_scaled['ID'].unique():
    obs_data = train_scaled[train_scaled['ID'] == obs_id]
    for i in range(len(obs_data) - sequence_length - output_steps + 1):
        seq = obs_data.iloc[i:i + sequence_length]
        target_seq = obs_data.iloc[i + sequence_length-1:i + sequence_length + output_steps-1]['FP'].values
        sequences.append(seq[numerical_features_withID].values)
        targets.append(target_seq)

# Convert to numpy arrays
X_train = np.array(sequences)  # Shape: (num_sequences, sequence_length, num_features)
y_train = np.array(targets)  

# Split data
X_features = X_train[:, :, :-1]  # numerical Features
X_obs_ids = X_train[:, :, -1]      # Observation_ID_encoded

test = pd.concat(all_plots)
test['ID_encoded'] = encoder.transform(test['ID'])

test_scaled = test.copy()
test_scaled[numerical_features] = scaler_x.transform(test[numerical_features])
test_scaled

FP   HR35_55     Riego      TMED  PREC        HR   
DateTime                                                                       
2023-07-21 10:00:00  -3.614804  0.585796  0.000000  0.510532   0.0  0.250270  \
2023-07-21 11:00:00  -2.526165  0.528868  0.258228  0.601499   0.0  0.194319   
2023-07-21 12:00:00  -3.653391  0.502404  0.126582  0.662310   0.0  0.152634   
2023-07-21 13:00:00  -8.117500  0.485460  0.000000  0.701132   0.0  0.118825   
2023-07-21 14:00:00  -9.626121  0.473581  0.000000  0.734190   0.0  0.083938   
...                        ...       ...       ...       ...   ...       ...   
2023-09-30 20:00:00 -14.322500  0.705606  0.000000  0.475931   0.0  0.282100   
2023-09-30 21:00:00 -12.811929  0.707335  0.000000  0.367229   0.0  0.382496   
2023-09-30 22:00:00 -11.750043  0.708917  0.000000  0.235710   0.0  0.541170   
2023-09-30 23:00:00 -11.012978  0.709535  0.000000  0.176590   0.0  0.616225   
2023-10-01 00:00:00 -10.360000  0.710114  0.000000  0.158901   0.0  0.646781   

                          RAD       DPV        VV       ETO  Hour_sin   Kc   
DateTime                                                                     
2023-07-21 10:00:00  0.504765  0.322311  0.158033  0.465367  0.853553  1.0  \
2023-07-21 11:00:00  0.703530  0.412610  0.140469  0.654406  0.750000  1.0   
2023-07-21 12:00:00  0.826375  0.484351  0.143718  0.782263  0.629410  1.0   
2023-07-21 13:00:00  0.909263  0.540813  0.170408  0.878227  0.500000  1.0   
2023-07-21 14:00:00  0.946513  0.596346  0.180879  0.927492  0.370590  1.0   
...                       ...       ...       ...       ...       ...  ...   
2023-09-30 20:00:00  0.023339  0.288523  0.112728  0.102749  0.017037  0.0   
2023-09-30 21:00:00  0.000000  0.205647  0.078046  0.041786  0.066987  0.0   
2023-09-30 22:00:00  0.000000  0.114617  0.076927  0.027647  0.146447  0.0   
2023-09-30 23:00:00  0.000000  0.082736  0.064703  0.018974  0.250000  0.0   
2023-10-01 00:00:00  0.000000  0.072864  0.063915  0.016789  0.370590  0.0   

                        ID   FP-lag1  ID_encoded  
DateTime                                          
2023-07-21 10:00:00  T1.1.  0.897742           0  
2023-07-21 11:00:00  T1.1.  0.898768           0  
2023-07-21 12:00:00  T1.1.  0.935445           0  
2023-07-21 13:00:00  T1.1.  0.897468           0  
2023-07-21 14:00:00  T1.1.  0.747069           0  
...                    ...       ...         ...  
2023-09-30 20:00:00  T4.2.  0.490398           6  
2023-09-30 21:00:00  T4.2.  0.538018           6  
2023-09-30 22:00:00  T4.2.  0.588911           6  
2023-09-30 23:00:00  T4.2.  0.624686           6  
2023-10-01 00:00:00  T4.2.  0.649518           6  

[17955 rows x 15 columns]

In [29]:
from keras_tuner import HyperModel
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, LSTM, Dense, Embedding, Concatenate

class LSTMHyperModel(HyperModel):
    def build(self, hp):
        # Inputs
        numerical_input = Input(shape=(sequence_length, len(numerical_features)), name='Numerical_Input')
        categorical_input = Input(shape=(sequence_length,), name='Categorical_Input')
        
        # Embedding layer for categorical feature
        embedding_dim = hp.Int('embedding_dim', min_value=4, max_value=20, step=4)  # Tune embedding dimension
        num_observations = train_scaled['ID_encoded'].nunique()
        categorical_embedding = Embedding(input_dim=num_observations, 
                                          output_dim=embedding_dim, 
                                          input_length=sequence_length)(categorical_input)
        
        # Concatenate inputs
        concatenated = Concatenate()([numerical_input, categorical_embedding])
        
        # LSTM layers
        lstm_units_1 = hp.Int('lstm_units_1', min_value=16, max_value=128, step=8)  # Tune units in 1st LSTM
        lstm_out_1 = LSTM(lstm_units_1, activation="relu", return_sequences=True)(concatenated)

        lstm_units_2 = hp.Int('lstm_units_2', min_value=8, max_value=64, step=4)  # Tune units in 2nd LSTM
        lstm_out_2 = LSTM(lstm_units_2, activation="relu", return_sequences=False)(lstm_out_1)
        

        # Dense layer for final output
        output = Dense(output_steps, activation='linear')(lstm_out_2)
        
        # Model
        model = Model(inputs=[numerical_input, categorical_input], outputs=output)
        
        # Compile
        learning_rate = hp.Float('learning_rate', min_value=1e-4, max_value=1e-2, sampling='log')  # Tune learning rate
        model.compile(optimizer=keras.optimizers.Adam(learning_rate=learning_rate), 
                      loss='mse', 
                      metrics=['mae'])
        
        return model

In [94]:
X_features_train, X_features_val, X_obs_ids_train, X_obs_ids_val, y_train_train, y_train_val = train_test_split(X_features, X_obs_ids, y_train, test_size=0.2, shuffle=True, random_state=123)

In [31]:
from keras_tuner import BayesianOptimization

# Initialize the tuner
tuner = BayesianOptimization(
    LSTMHyperModel(),
    objective='val_loss',  # Optimize for validation loss
    max_trials=20,         # Number of hyperparameter combinations to try
    executions_per_trial=1,  # Average results over 2 runs for each configuration
    directory='tuner_logs',  # Directory to save tuning logs
    project_name='lstm_hyperparameter_tuning_bayesian_12h',
    seed=1234
)

tuner.search(
    x=[X_features_train, X_obs_ids_train],
    y=y_train_train,
    validation_data=([X_features_val, X_obs_ids_val], y_train_val),
    epochs=70,
    batch_size=32,
    #callbacks=[tf.keras.callbacks.EarlyStopping(monitor='val_loss', patience=10)]  # Early stopping
)

Reloading Tuner from tuner_logs\lstm_hyperparameter_tuning_bayesian_12h\tuner0.json


In [32]:
lstm_12h = tuner.get_best_models()[0]
lstm_12h.summary()

Model: "model"
__________________________________________________________________________________________________
 Layer (type)                Output Shape                 Param #   Connected to                  
 Categorical_Input (InputLa  [(None, 12)]                 0         []                            
 yer)                                                                                             
                                                                                                  
 Numerical_Input (InputLaye  [(None, 12, 12)]             0         []                            
 r)                                                                                               
                                                                                                  
 embedding (Embedding)       (None, 12, 12)               84        ['Categorical_Input[0][0]']   
                                                                                              

In [117]:


r2s = []
maes = []
rmses = []
cvrmses = []



for id in test_scaled['ID'].unique():
    print(id)

    # Get df of corresponding plot
    df_plot = test_scaled[test_scaled['ID'] == id]
    
    sequences = []
    targets = []

    # create sequences
    for obs_id in df_plot['ID'].unique():
        obs_data = df_plot[df_plot['ID'] == obs_id]
        for i in range(len(obs_data) - sequence_length - output_steps + 1):
            seq = obs_data.iloc[i:i + sequence_length]
            target_seq = obs_data.iloc[i + sequence_length:i + sequence_length + output_steps]['FP'].values
            sequences.append(seq[numerical_features_withID].values)
            targets.append(target_seq)

    # Convert to numpy arrays
    X_test = np.array(sequences)  # Shape: (num_sequences, sequence_length, num_features)
    y_test = np.array(targets)  
    
    # Split numerical/categorical input
    X_features = X_test[:, :, :-1]  # numerical Features
    X_obs_ids = X_test[:, :, -1]      # Observation_ID_encoded

    # Make predictions on the test set
    y_pred = lstm_12h.predict([X_features, X_obs_ids])
    y_pred = scaler_y.inverse_transform(y_pred)
    
    # Convert the unit bars to MPa
    y_pred = y_pred * 0.1
    y_test = y_test * 0.1
    
    #display(y_pred)

    # Initialize lists to store metrics for each step
    mae_per_step = []
    rmse_per_step = []
    r2_per_step = []
    cvrmse_per_step = []

    # Loop through each output step
    for step in range(output_steps):
        mae = mean_absolute_error(y_test[:, step], y_pred[:, step])  # MAE for step
        mae_per_step.append(mae)
        rmse = mean_squared_error(y_test[:, step], y_pred[:, step], squared=False)  # MAE for step
        rmse_per_step.append(rmse)
        r2 = np.corrcoef(y_test[:, step], y_pred[:, step])[0][1]**2  # R2 for step
        r2_per_step.append(r2)
        cvrmse = CVRMSE(y_test[:, step], y_pred[:, step])  # CVRMSE for step
        cvrmse_per_step.append(cvrmse)
        print(f"Step {step + 1}- R2: {r2:.4f} - MAE: {mae:.4f} - RMSE: {rmse:.4f} - CVRMSE: {cvrmse:.4f}")

    # Average metrics across all steps
    average_r2 = sum(r2_per_step) / output_steps
    r2s.append(average_r2)
    average_mae = sum(mae_per_step) / output_steps
    maes.append(average_mae)
    average_rmse = sum(rmse_per_step) / output_steps
    rmses.append(average_rmse)
    average_cvrmse = sum(cvrmse_per_step) / output_steps
    cvrmses.append(average_cvrmse)

    print("\nOverall Metrics:")
    print(f"Average R2 across all steps: {average_r2:.4f}")
    print(f"Average MAE across all steps: {average_mae:.4f}")
    print(f"Average RMSE across all steps: {average_rmse:.4f}")
    print(f"Average CVRMSE across all steps: {average_cvrmse:.4f}\n\n")



T1.1.
53/53 [==============================] - 0s 3ms/step
Step 1- R2: 0.9520 - MAE: 0.0752 - RMSE: 0.0964 - CVRMSE: -7.6268
Step 2- R2: 0.9463 - MAE: 0.0794 - RMSE: 0.1019 - CVRMSE: -8.0563
Step 3- R2: 0.9379 - MAE: 0.0854 - RMSE: 0.1095 - CVRMSE: -8.6359
Step 4- R2: 0.9328 - MAE: 0.0888 - RMSE: 0.1148 - CVRMSE: -8.9975
Step 5- R2: 0.9220 - MAE: 0.0947 - RMSE: 0.1237 - CVRMSE: -9.6965
Step 6- R2: 0.9151 - MAE: 0.0986 - RMSE: 0.1299 - CVRMSE: -10.1426
Step 7- R2: 0.9125 - MAE: 0.0985 - RMSE: 0.1318 - CVRMSE: -10.3044
Step 8- R2: 0.9062 - MAE: 0.1010 - RMSE: 0.1363 - CVRMSE: -10.7165
Step 9- R2: 0.8999 - MAE: 0.1039 - RMSE: 0.1409 - CVRMSE: -11.0127
Step 10- R2: 0.8958 - MAE: 0.1070 - RMSE: 0.1449 - CVRMSE: -11.2262
Step 11- R2: 0.8852 - MAE: 0.1138 - RMSE: 0.1539 - CVRMSE: -11.8482
Step 12- R2: 0.8748 - MAE: 0.1187 - RMSE: 0.1625 - CVRMSE: -12.4224

Overall Metrics:
Average R2 across all steps: 0.9150
Average MAE across all steps: 0.0971
Average RMSE across all steps: 0.1289
Average CV

In [118]:
# Overall metrics
print('R2:', np.mean(r2s))
print('MAE:',np.mean(maes))
print('RMSE:',np.mean(rmses))
print('CVRMSE:',np.mean(cvrmses))

R2: 0.9130061200874856
MAE: 0.1045372265119736
RMSE: 0.15003747596067418
CVRMSE: -14.78985891098885


In [95]:
lstm_12h.evaluate([X_features_val, X_obs_ids_val], y_train_val)

78/78 [==============================] - 1s 3ms/step - loss: 3.0259e-04 - mae: 0.0125


[0.0003025866753887385, 0.012534347362816334]

# 24h

In [119]:
output_steps = 24  # Number of steps to predict
sequence_length = 12
sequences = []
targets = []

numerical_features_withID = ['HR35_55', 'Riego', 'TMED', 'PREC', 'HR', 'RAD', 'DPV', 'VV', 'ETO', 'Hour_sin', 'Kc', 'FP-lag1', 'ID_encoded']

for obs_id in train_scaled['ID'].unique():
    obs_data = train_scaled[train_scaled['ID'] == obs_id]
    for i in range(len(obs_data) - sequence_length - output_steps + 1):
        seq = obs_data.iloc[i:i + sequence_length]
        target_seq = obs_data.iloc[i + sequence_length-1:i + sequence_length + output_steps-1]['FP'].values
        sequences.append(seq[numerical_features_withID].values)
        targets.append(target_seq)

# Convert to numpy arrays
X_train = np.array(sequences)  # Shape: (num_sequences, sequence_length, num_features)
y_train = np.array(targets)  

# Split data
X_features = X_train[:, :, :-1]  # numerical Features
X_obs_ids = X_train[:, :, -1]      # Observation_ID_encoded

test = pd.concat(all_plots)
test['ID_encoded'] = encoder.transform(test['ID'])

test_scaled = test.copy()
test_scaled[numerical_features] = scaler_x.transform(test[numerical_features])
test_scaled

FP   HR35_55     Riego      TMED  PREC        HR   
DateTime                                                                       
2023-07-21 10:00:00  -3.614804  0.585796  0.000000  0.510532   0.0  0.250270  \
2023-07-21 11:00:00  -2.526165  0.528868  0.258228  0.601499   0.0  0.194319   
2023-07-21 12:00:00  -3.653391  0.502404  0.126582  0.662310   0.0  0.152634   
2023-07-21 13:00:00  -8.117500  0.485460  0.000000  0.701132   0.0  0.118825   
2023-07-21 14:00:00  -9.626121  0.473581  0.000000  0.734190   0.0  0.083938   
...                        ...       ...       ...       ...   ...       ...   
2023-09-30 20:00:00 -14.322500  0.705606  0.000000  0.475931   0.0  0.282100   
2023-09-30 21:00:00 -12.811929  0.707335  0.000000  0.367229   0.0  0.382496   
2023-09-30 22:00:00 -11.750043  0.708917  0.000000  0.235710   0.0  0.541170   
2023-09-30 23:00:00 -11.012978  0.709535  0.000000  0.176590   0.0  0.616225   
2023-10-01 00:00:00 -10.360000  0.710114  0.000000  0.158901   0.0  0.646781   

                          RAD       DPV        VV       ETO  Hour_sin   Kc   
DateTime                                                                     
2023-07-21 10:00:00  0.504765  0.322311  0.158033  0.465367  0.853553  1.0  \
2023-07-21 11:00:00  0.703530  0.412610  0.140469  0.654406  0.750000  1.0   
2023-07-21 12:00:00  0.826375  0.484351  0.143718  0.782263  0.629410  1.0   
2023-07-21 13:00:00  0.909263  0.540813  0.170408  0.878227  0.500000  1.0   
2023-07-21 14:00:00  0.946513  0.596346  0.180879  0.927492  0.370590  1.0   
...                       ...       ...       ...       ...       ...  ...   
2023-09-30 20:00:00  0.023339  0.288523  0.112728  0.102749  0.017037  0.0   
2023-09-30 21:00:00  0.000000  0.205647  0.078046  0.041786  0.066987  0.0   
2023-09-30 22:00:00  0.000000  0.114617  0.076927  0.027647  0.146447  0.0   
2023-09-30 23:00:00  0.000000  0.082736  0.064703  0.018974  0.250000  0.0   
2023-10-01 00:00:00  0.000000  0.072864  0.063915  0.016789  0.370590  0.0   

                        ID   FP-lag1  ID_encoded  
DateTime                                          
2023-07-21 10:00:00  T1.1.  0.897742           0  
2023-07-21 11:00:00  T1.1.  0.898768           0  
2023-07-21 12:00:00  T1.1.  0.935445           0  
2023-07-21 13:00:00  T1.1.  0.897468           0  
2023-07-21 14:00:00  T1.1.  0.747069           0  
...                    ...       ...         ...  
2023-09-30 20:00:00  T4.2.  0.490398           6  
2023-09-30 21:00:00  T4.2.  0.538018           6  
2023-09-30 22:00:00  T4.2.  0.588911           6  
2023-09-30 23:00:00  T4.2.  0.624686           6  
2023-10-01 00:00:00  T4.2.  0.649518           6  

[17955 rows x 15 columns]

In [36]:
from keras_tuner import HyperModel
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, LSTM, Dense, Embedding, Concatenate

class LSTMHyperModel(HyperModel):
    def build(self, hp):
        # Inputs
        numerical_input = Input(shape=(sequence_length, len(numerical_features)), name='Numerical_Input')
        categorical_input = Input(shape=(sequence_length,), name='Categorical_Input')
        
        # Embedding layer for categorical feature
        embedding_dim = hp.Int('embedding_dim', min_value=4, max_value=20, step=4)  # Tune embedding dimension
        num_observations = train_scaled['ID_encoded'].nunique()
        categorical_embedding = Embedding(input_dim=num_observations, 
                                          output_dim=embedding_dim, 
                                          input_length=sequence_length)(categorical_input)
        
        # Concatenate inputs
        concatenated = Concatenate()([numerical_input, categorical_embedding])
        
        # LSTM layers
        lstm_units_1 = hp.Int('lstm_units_1', min_value=16, max_value=128, step=8)  # Tune units in 1st LSTM
        lstm_out_1 = LSTM(lstm_units_1, activation="relu", return_sequences=True)(concatenated)

        lstm_units_2 = hp.Int('lstm_units_2', min_value=8, max_value=64, step=4)  # Tune units in 2nd LSTM
        lstm_out_2 = LSTM(lstm_units_2, activation="relu", return_sequences=False)(lstm_out_1)
        

        # Dense layer for final output
        output = Dense(output_steps, activation='linear')(lstm_out_2)
        
        # Model
        model = Model(inputs=[numerical_input, categorical_input], outputs=output)
        
        # Compile
        learning_rate = hp.Float('learning_rate', min_value=1e-4, max_value=1e-2, sampling='log')  # Tune learning rate
        model.compile(optimizer=keras.optimizers.Adam(learning_rate=learning_rate), 
                      loss='mse', 
                      metrics=['mae'])
        
        return model

In [97]:
X_features_train, X_features_val, X_obs_ids_train, X_obs_ids_val, y_train_train, y_train_val = train_test_split(X_features, X_obs_ids, y_train, test_size=0.2, shuffle=True, random_state=123)

In [38]:
from keras_tuner import BayesianOptimization

# Initialize the tuner
tuner = BayesianOptimization(
    LSTMHyperModel(),
    objective='val_loss',  # Optimize for validation loss
    max_trials=20,         # Number of hyperparameter combinations to try
    executions_per_trial=1,  # Average results over 2 runs for each configuration
    directory='tuner_logs',  # Directory to save tuning logs
    project_name='lstm_hyperparameter_tuning_bayesian_24h',
    seed=1234
)

tuner.search(
    x=[X_features_train, X_obs_ids_train],
    y=y_train_train,
    validation_data=([X_features_val, X_obs_ids_val], y_train_val),
    epochs=70,
    batch_size=32,
    #callbacks=[tf.keras.callbacks.EarlyStopping(monitor='val_loss', patience=10)]  # Early stopping
)

Reloading Tuner from tuner_logs\lstm_hyperparameter_tuning_bayesian_24h\tuner0.json


In [39]:
lstm_24h = tuner.get_best_models()[0]
lstm_24h.summary()

Model: "model"
__________________________________________________________________________________________________
 Layer (type)                Output Shape                 Param #   Connected to                  
 Categorical_Input (InputLa  [(None, 12)]                 0         []                            
 yer)                                                                                             
                                                                                                  
 Numerical_Input (InputLaye  [(None, 12, 12)]             0         []                            
 r)                                                                                               
                                                                                                  
 embedding (Embedding)       (None, 12, 8)                56        ['Categorical_Input[0][0]']   
                                                                                              

In [120]:


r2s = []
maes = []
rmses = []
cvrmses = []



for id in test_scaled['ID'].unique():
    print(id)

    # Get df of corresponding plot
    df_plot = test_scaled[test_scaled['ID'] == id]
    
    sequences = []
    targets = []

    # create sequences
    for obs_id in df_plot['ID'].unique():
        obs_data = df_plot[df_plot['ID'] == obs_id]
        for i in range(len(obs_data) - sequence_length - output_steps + 1):
            seq = obs_data.iloc[i:i + sequence_length]
            target_seq = obs_data.iloc[i + sequence_length:i + sequence_length + output_steps]['FP'].values
            sequences.append(seq[numerical_features_withID].values)
            targets.append(target_seq)

    # Convert to numpy arrays
    X_test = np.array(sequences)  # Shape: (num_sequences, sequence_length, num_features)
    y_test = np.array(targets)  
    
    # Split numerical/categorical input
    X_features = X_test[:, :, :-1]  # numerical Features
    X_obs_ids = X_test[:, :, -1]      # Observation_ID_encoded

    # Make predictions on the test set
    y_pred = lstm_24h.predict([X_features, X_obs_ids])
    y_pred = scaler_y.inverse_transform(y_pred)
    
    # Convert the unit bars to MPa
    y_pred = y_pred * 0.1
    y_test = y_test * 0.1
    
    #display(y_pred)

    # Initialize lists to store metrics for each step
    mae_per_step = []
    rmse_per_step = []
    r2_per_step = []
    cvrmse_per_step = []

    # Loop through each output step
    for step in range(output_steps):
        mae = mean_absolute_error(y_test[:, step], y_pred[:, step])  # MAE for step
        mae_per_step.append(mae)
        rmse = mean_squared_error(y_test[:, step], y_pred[:, step], squared=False)  # MAE for step
        rmse_per_step.append(rmse)
        r2 = np.corrcoef(y_test[:, step], y_pred[:, step])[0][1]**2  # R2 for step
        r2_per_step.append(r2)
        cvrmse = CVRMSE(y_test[:, step], y_pred[:, step])  # CVRMSE for step
        cvrmse_per_step.append(cvrmse)
        print(f"Step {step + 1}- R2: {r2:.4f} - MAE: {mae:.4f} - RMSE: {rmse:.4f} - CVRMSE: {cvrmse:.4f}")

    # Average metrics across all steps
    average_r2 = sum(r2_per_step) / output_steps
    r2s.append(average_r2)
    average_mae = sum(mae_per_step) / output_steps
    maes.append(average_mae)
    average_rmse = sum(rmse_per_step) / output_steps
    rmses.append(average_rmse)
    average_cvrmse = sum(cvrmse_per_step) / output_steps
    cvrmses.append(average_cvrmse)

    print("\nOverall Metrics:")
    print(f"Average R2 across all steps: {average_r2:.4f}")
    print(f"Average MAE across all steps: {average_mae:.4f}")
    print(f"Average RMSE across all steps: {average_rmse:.4f}")
    print(f"Average CVRMSE across all steps: {average_cvrmse:.4f}\n\n")



T1.1.
53/53 [==============================] - 0s 4ms/step
Step 1- R2: 0.9456 - MAE: 0.0827 - RMSE: 0.1025 - CVRMSE: -8.0941
Step 2- R2: 0.9397 - MAE: 0.0861 - RMSE: 0.1084 - CVRMSE: -8.5286
Step 3- R2: 0.9357 - MAE: 0.0887 - RMSE: 0.1123 - CVRMSE: -8.8034
Step 4- R2: 0.9303 - MAE: 0.0920 - RMSE: 0.1164 - CVRMSE: -9.1475
Step 5- R2: 0.9244 - MAE: 0.0957 - RMSE: 0.1220 - CVRMSE: -9.5277
Step 6- R2: 0.9234 - MAE: 0.0956 - RMSE: 0.1224 - CVRMSE: -9.5646
Step 7- R2: 0.9179 - MAE: 0.0976 - RMSE: 0.1265 - CVRMSE: -9.8978
Step 8- R2: 0.9100 - MAE: 0.1020 - RMSE: 0.1327 - CVRMSE: -10.3684
Step 9- R2: 0.9052 - MAE: 0.1036 - RMSE: 0.1356 - CVRMSE: -10.6077
Step 10- R2: 0.8963 - MAE: 0.1074 - RMSE: 0.1430 - CVRMSE: -11.1359
Step 11- R2: 0.8907 - MAE: 0.1091 - RMSE: 0.1458 - CVRMSE: -11.3801
Step 12- R2: 0.8866 - MAE: 0.1099 - RMSE: 0.1477 - CVRMSE: -11.5656
Step 13- R2: 0.8874 - MAE: 0.1104 - RMSE: 0.1477 - CVRMSE: -11.5247
Step 14- R2: 0.8864 - MAE: 0.1119 - RMSE: 0.1477 - CVRMSE: -11.5596
Step 

In [121]:
# Overall metrics
print('R2:', np.mean(r2s))
print('MAE:',np.mean(maes))
print('RMSE:',np.mean(rmses))
print('CVRMSE:',np.mean(cvrmses))

R2: 0.893240376017765
MAE: 0.11556895636173911
RMSE: 0.16725994696681598
CVRMSE: -16.64698533937422


In [98]:
lstm_24h.evaluate([X_features_val, X_obs_ids_val], y_train_val)

77/77 [==============================] - 1s 4ms/step - loss: 3.0627e-04 - mae: 0.0128


[0.00030627386877313256, 0.012787655927240849]